In [4]:
from dataprocess.kdd_cup99 import KDD_CUP_99_DataLoader
from net.CNN_KDD import CNN_KDD
from net.multCNN import multCNN

In [5]:
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.utils.tensorboard import SummaryWriter

In [6]:
import os 
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"]='0'

device=torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(device)

cuda


In [7]:
dataset = KDD_CUP_99_DataLoader('E:/DataSets/kddcup.data', 256, 'Test')
discrete_column_idx = dataset.data.discrete_column
discrete_column_idx.remove(41)
continuous_column_idx = [i for i in range(41) if i not in discrete_column_idx]
input_channel_kind = len(discrete_column_idx)
input_channel_num = len(continuous_column_idx)

In [8]:
net = multCNN(input_channel_num, input_channel_kind, 23).to(device)
checkpoint = torch.load('\Transfer-learning-IDS\history\CNN_KDD\checkpoint\ckpt_best_99.pth')
net.load_state_dict(checkpoint['net'])

<All keys matched successfully>

In [11]:
with torch.no_grad():
    num = 0
    num_dif = 0
    for step, (x, y) in enumerate(dataset):
        x_continuous, x_discrete =x[:, continuous_column_idx], x[:, discrete_column_idx]
        x_continuous = x_continuous.to(device)
        x_discrete = x_discrete.to(device)
        print('label', F.one_hot(y.long(), num_classes=23))

        y_pred = net((x_continuous, x_discrete))
        y_pred = y_pred.cpu()
        print('logits', y_pred)

        y_pred = torch.argmax(y_pred, 1)
        compare = y_pred != y
        num += y_pred.shape[0]
        num_dif += compare.sum().item()

accuracy = (num - num_dif) / num
print(accuracy)

label tensor([[1, 0, 0,  ..., 0, 0, 0],
        [0, 0, 1,  ..., 0, 0, 0],
        [0, 1, 0,  ..., 0, 0, 0],
        ...,
        [1, 0, 0,  ..., 0, 0, 0],
        [0, 0, 1,  ..., 0, 0, 0],
        [1, 0, 0,  ..., 0, 0, 0]])
logits tensor([[ 60.6213, -61.4980,  30.6097,  ...,   4.3634,   2.4200,  -4.4999],
        [ 11.1367, -48.8256,  23.4588,  ...,   7.0297,  -0.1549,  -4.7210],
        [-38.1362,  36.3709,   0.8995,  ...,  -5.0464,  -0.2589,   3.8429],
        ...,
        [ 60.6213, -61.4980,  30.6097,  ...,   4.3634,   2.4200,  -4.4999],
        [-32.2776,  -9.9497,  21.9835,  ...,  -0.1222,   5.5124,   4.5249],
        [ 60.6213, -61.4980,  30.6097,  ...,   4.3634,   2.4200,  -4.4999]])
label tensor([[1, 0, 0,  ..., 0, 0, 0],
        [1, 0, 0,  ..., 0, 0, 0],
        [0, 0, 1,  ..., 0, 0, 0],
        ...,
        [0, 1, 0,  ..., 0, 0, 0],
        [1, 0, 0,  ..., 0, 0, 0],
        [1, 0, 0,  ..., 0, 0, 0]])
logits tensor([[ 60.6213, -61.4980,  30.6097,  ...,   4.3634,   2.4200,  -4